In [ ]:
import pyreadstat
import pandas as pd
import numpy as np
import networkx as nx
import warnings
import itertools
from tqdm impot tqdm

In [25]:
df, meta = pyreadstat.read_sav("..//data/raw/OD 2017//Banco de Dados//OD_2017.sav")
df.drop_duplicates(subset=['zona', 'zona_esc', 'zonatra1', 'id_pess'], inplace=True)

In [26]:
df = df[df['muni_dom'] == 36]
max_zona = int(df.zona.max())

In [33]:
zone_nodes = pd.DataFrame(np.zeros(max_zona+1), columns=['zone'])
zone_nodes['zone'] = zone_nodes.index + 1

trab_esc = df[['zona', 'zona_esc', 'zonatra1', 'id_pess', 'id_dom']].copy()
trab_esc.rename(columns={'zona':'home_zone',
                        'zona_esc':'school',
                        'zonatra1':'work',
                        'id_pess': 'id', 'id_dom': 'house_id'}, inplace=True)

trab_esc = trab_esc[~(trab_esc['work'] > max_zona) & 
        ~(trab_esc['school'] > max_zona) & ~(trab_esc['home_zone'] > max_zona)].reset_index(drop=True)

# Remover pessoas sem trabalho ou escola?
#trab_esc[~(trab_esc['school'].isna() & trab_esc['work'].isna())]

In [55]:
def add_person_to_graph(person):
    G.add_node(person['id'])
    
def add_home_zone_edge(person):
    if  pd.notna(person['home_zone']):
        G.add_edge(person['id'], person['home_zone'])
        G.edges[person['id'], person['home_zone']].update({'type':'home_zone'})
    else: 
        warnings.warn(f"Warning Person {person['id']} has no Home! :(")
        
def add_household_edge(person1, person2):
        G.add_edge(person1, person2)
        G.edges[person1, person2].update({'type':'household'})

def add_work_edge(person):
    if  pd.notna(person['work']):
        G.add_edge(person['id'], person['work'])
        G.edges[person['id'], person['work']].update({'type':'work'})
        
def add_school_edge(person):
    if pd.notna(person['school']):
        G.add_edge(person['id'], person['school'])
        G.edges[person['id'], person['school']].update({'type':'school'})

In [22]:
G = nx.from_numpy_matrix(pd.get_dummies(zone_nodes['zone']).values)

print('Criando Zonas')
print(len(G.nodes))
print(len(G.edges))
print(50*'*')

trab_esc.apply(add_node_to_graph, axis=1)
print('Adicionando Pessoas')
print(len(G.nodes))
print(len(G.edges))
print(50*'*')

trab_esc.apply(add_home_zone_edge, axis=1)
print('Adicionando Vertices de Zonas das Casas')
print(len(G.nodes))
print(len(G.edges))
print(50*'*')

trab_esc.apply(add_work_edge, axis=1)
print('Adicionando Vertices de Trabalhos')
print(len(G.nodes))
print(len(G.edges))
print(50*'*')

trab_esc.apply(add_school_edge, axis=1)
print('Adicionando Vertices de Escolas')
print(len(G.nodes))
print(len(G.edges))
print(50*'*')

Criando Zonas
343
343
**************************************************
Adicionando Pessoas
55835
343
**************************************************
Adicionando Vertices de Casas
55835
55835
**************************************************
Adicionando Vertices de Trabalhos
55835
73262
**************************************************
Adicionando Vertices de Escolas
55835
81490
**************************************************


In [7]:
G.nodes

NodeView((0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80, 81, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91, 92, 93, 94, 95, 96, 97, 98, 99, 100, 101, 102, 103, 104, 105, 106, 107, 108, 109, 110, 111, 112, 113, 114, 115, 116, 117, 118, 119, 120, 121, 122, 123, 124, 125, 126, 127, 128, 129, 130, 131, 132, 133, 134, 135, 136, 137, 138, 139, 140, 141, 142, 143, 144, 145, 146, 147, 148, 149, 150, 151, 152, 153, 154, 155, 156, 157, 158, 159, 160, 161, 162, 163, 164, 165, 166, 167, 168, 169, 170, 171, 172, 173, 174, 175, 176, 177, 178, 179, 180, 181, 182, 183, 184, 185, 186, 187, 188, 189, 190, 191, 192, 193, 194, 195, 196, 197, 198, 199, 200, 201, 202, 203, 204, 205, 206, 207, 208, 209, 210, 211, 212, 213, 214, 215, 216, 217, 218, 219, 

In [9]:
nx.write_gpickle(G, 'Grafo_Zonas_SP.gpickle')

In [10]:
G_r = nx.read_gpickle('Grafo_Zonas_SP.gpickle')

In [ ]:
print('Adicionando Vertices de Casas')

def add_edge(person1, person2, edge_type, edge_zone):
        G.add_edge(person1, person2)
        G.edges[person1, person2].update({'type':edge_type, 'zone': edge_zone})
        
for h in tqdm(trab_esc['house_id'].unique()):
    tmp = trab_esc[trab_esc['house_id'] == h]
    zone = tmp['home_zone'].value_counts().iloc[0]
    if len(tmp) > 1:
        for p1, p2 in list(itertools.combinations(tmp['id'].values, 2)):
            add_edge(p1, p2, 'house', zone)


print(len(G.nodes))
print(len(G.edges))
print(50*'*')

Adicionando Vertices de Escolas


EdgeDataView([(0, 0, {'weight': 1}), (1, 1, {'weight': 1}), (1, '00010001101', {'type': 'home_zone'}), (1, '00010001102', {'type': 'home_zone'}), (1, '00010002101', {'type': 'work'}), (1, '00010002102', {'type': 'work'}), (1, '00010002103', {'type': 'home_zone'}), (1, '00010002104', {'type': 'home_zone'}), (1, '00010003101', {'type': 'home_zone'}), (1, '00010003102', {'type': 'home_zone'}), (1, '00010005101', {'type': 'home_zone'}), (1, '00010008101', {'type': 'home_zone'}), (1, '00010008102', {'type': 'home_zone'}), (1, '00010009101', {'type': 'home_zone'}), (1, '00010009102', {'type': 'home_zone'}), (1, '00010009103', {'type': 'home_zone'}), (1, '00010010101', {'type': 'home_zone'}), (1, '00010011101', {'type': 'home_zone'}), (1, '00010011102', {'type': 'home_zone'}), (1, '00010012101', {'type': 'home_zone'}), (1, '00010012102', {'type': 'home_zone'}), (1, '00010013101', {'type': 'home_zone'}), (1, '00010015102', {'type': 'work'}), (1, '00010018101', {'type': 'home_zone'}), (1, '0001